In [2]:
!pip install aiofiles

Defaulting to user installation because normal site-packages is not writeable
  Obtaining dependency information for aiofiles from https://files.pythonhosted.org/packages/c5/19/5af6804c4cc0fed83f47bff6e413a98a36618e7d40185cd36e69737f3b0e/aiofiles-23.2.1-py3-none-any.whl.metadata
  Obtaining dependency information for jsonlines from https://files.pythonhosted.org/packages/f8/62/d9ba6323b9202dd2fe166beab8a86d29465c41a0288cbe229fac60c1ab8d/jsonlines-4.0.0-py3-none-any.whl.metadata

[notice] A new release of pip is available: 23.2.1 -> 23.3.1
[notice] To update, run: pip install --upgrade pip


In [3]:
import os
from glob import glob
import aiofiles

output_dir = os.path.abspath("./output_tryagain")

jsonfiles = glob(os.path.join(output_dir, "*.json"))

len(jsonfiles)

1684

In [2]:
# import json

# decodeerrors = {}
# deleted = []
# nocontent = []
# with_metadata = {}

# async def layers_with_metadata():
#     async def _check(f):
#         delete = False
#         async with aiofiles.open(f, 'r') as infile:
#             content = await infile.read()
#             if content:
#                 data = json.loads(content)
#                 if 'metadata' not in data:
#                     delete = True
#                 else:
#                     with_metadata[f] = data
#             else:
#                 nocontent.append(f)
#                 delete = True
#         if delete:
#             deleted.append(f)
#             os.remove(f)
#     return await asyncio.gather(*[_check(f) for f in jsonfiles])

# import asyncio
# import nest_asyncio

# nest_asyncio.apply()

In [4]:
import asyncio
import json

async def read_data():
    async def _read(f):
        async with aiofiles.open(f, 'r') as infile:
            content = await infile.read()
            return json.loads(content)
    tasks = [_read(f) for f in jsonfiles]
    return await asyncio.gather(*tasks)


In [6]:
import nest_asyncio

nest_asyncio.apply()

In [88]:
%%time

data = asyncio.run(read_data())

CPU times: user 2min 41s, sys: 23 s, total: 3min 4s
Wall time: 2min 50s


In [89]:
docs = {
    "servers": [],
    "services": [],
    "layers": [],
}

for server in data:
    server_md = server['metadata']
    server_url = server_md['url']
    server_hash = hash(server_md['url'])
    server_md['hash'] = server_hash
    for a in ('folders', 'services'):
        if a in server_md:
            del server_md[a]
    docs["servers"].append(server_md)

    for service in server['services']:
        service_md = service['metadata']
        service_name = service_md['name'] = service['name']
        service_url = service_md['url'] = service['url']
        service_md['server_url'] = server_url
        service_hash = hash(service_url)
        service_md['hash'] = service_hash
        service_md['server_hash'] = server_hash
        layers = service_md['layers']
        del service_md['layers']
        docs['services'].append(service_md)

        for layer_md in layers:
            layer_md['server_url'] = server_url
            layer_md['service_name'] = service_name
            layer_md['service_url'] = service_url
            layer_hash = hash(layer_md['url'])
            layer_md['hash'] = layer_hash
            layer_md['server_hash'] = server_hash
            layer_md['service_hash'] = service_hash
            
            docs['layers'].append(layer_md)

In [124]:
layerdict = {}
for l in docs['layers']:
    if 'type' in l:
        if l['type'] not in layerdict:
            layerdict[l['type']] = []
        layerdict[l['type']].append(l)

In [125]:
layerdict.keys()

dict_keys(['Raster Layer', 'Group Layer', 'Feature Layer', 'Annotation Layer', 'Annotation SubLayer', 'Mosaic Layer', 'Raster Catalog Layer', 'Terrain Layer', 'Network Analysis Layer', 'Network Dataset Layer', 'Parcel Layer', 'Topology Layer', 'Mosiac Layer', 'Image Service Layer', 'Annotation Sublayer', 'Dimension Layer', 'Tin Layer', 'Table'])

In [163]:
%%time

server_df = pd.DataFrame(docs['servers']).astype(str).apply(lambda s: s.str.strip().replace('', None)).dropna(axis=1, how='all').astype(str)
server_df.dropna(axis=1, how='all').to_parquet('servers.parquet')

CPU times: user 37 ms, sys: 1.28 ms, total: 38.3 ms
Wall time: 51.8 ms


In [164]:
%%time

services_df = pd.DataFrame(docs['services']).astype(str).apply(lambda s: s.str.strip().replace('', None)).dropna(axis=1, how='all').astype(str)
services_df.astype(str).to_parquet('services.parquet')

CPU times: user 34.3 s, sys: 1.94 s, total: 36.3 s
Wall time: 37.3 s


In [158]:
layer_df = pd.DataFrame(docs['layers'])

In [165]:
%%time

layer_df.astype(str).apply(lambda s: s.str.strip().replace('', None)).dropna(axis=1, how='all').astype(str).to_parquet('layers.parquet')

CPU times: user 2min 36s, sys: 25.7 s, total: 3min 1s
Wall time: 3min 10s
